### Dogpark_Sweden3

* issue 10
* Notebook [ ](https://github.com/salgo60/Dogpark_Sweden/blob/main/notebook/10%20Stockholmsstad.ipynb)

In [1]:
import time
import datetime  
start_time = time.time()
start_str = datetime.datetime.now().strftime("%Y-%m-%d %H:%M")
print(f"Started: {start_str}")


Started: 2025-10-07 17:34


In [2]:
import requests, json, time, os
from bs4 import BeautifulSoup
OFFLINE_MODE = True

if OFFLINE_MODE:
    print("🚫 Offline-läge: inga nya data hämtas.")
    with open("hundparker_umap.geojson", "r", encoding="utf-8") as f:
        geojson = json.load(f)
    features = geojson["features"]
else:
    BASE_URL = "https://www.hundlistan.se/"
    OUTFILE = "hundparker_umap.geojson"
    
    params = {
        "mylisting-ajax": "1",
        "action": "get_listings",
        "security": "5e528da4d5",
        "form_data[preserve_page]": "true",
        "form_data[sort]": "latest",
        "form_data[region]": "",
        "form_data[search_location]": "",
        "form_data[lat]": "false",
        "form_data[lng]": "false",
        "listing_type": "hundpark",
        "listing_wrap": "col-md-12 grid-item"
    }
    
    # --- Om filen redan finns, ladda tidigare resultat (så du kan återuppta)
    if os.path.exists(OUTFILE):
        with open(OUTFILE, "r", encoding="utf-8") as f:
            geojson = json.load(f)
        features = geojson.get("features", [])
        print(f"🔁 Återupptar från tidigare körning ({len(features)} poster hittade).")
    else:
        features = []
    
    for page in range(1, 40):
        params["form_data[page]"] = str(page)
        print(f"Hämtar sida {page}/39 ...", end="\r")
    
        try:
            r = requests.get(BASE_URL, params=params, timeout=15)
            r.raise_for_status()
        except Exception as e:
            print(f"\n⚠️ Sida {page} misslyckades: {e}")
            continue
    
        data = r.json()
        soup = BeautifulSoup(data.get("html", ""), "html.parser")
    
        items = soup.select(".lf-item-container")
        if not items:
            print(f"\nℹ️ Inga fler resultat på sida {page}. Avslutar.")
            break
    
        for item in items:
            try:
                data_id = item.get("data-id")
                if any(f["properties"]["id"] == data_id for f in features):
                    continue  # hoppa över redan sparad post
    
                title = item.select_one(".listing-preview-title").get_text(strip=True)
                href = item.select_one("a")["href"]
                lan = item.select_one(".lf-contact li").get_text(strip=True)
                loc = json.loads(item.get("data-locations"))[0]
                address = loc.get("address")
                lat, lng = float(loc.get("lat")), float(loc.get("lng"))
    
                # --- Hämta detaljsida för "Hemsida"
                hemsida_url = None
                try:
                    detail = requests.get(href, timeout=10)
                    if detail.status_code == 200:
                        detail_soup = BeautifulSoup(detail.text, "html.parser")
                        hemsida_link = detail_soup.select_one("a[href*='http']:contains('Hemsida')")
                        if hemsida_link:
                            hemsida_url = hemsida_link["href"]
                except Exception as e:
                    print(f"⚠️ Kunde inte hämta detaljer för {title}: {e}")
    
                popup_html = f"""
                <b>{title}</b><br>
                {address}<br>
                {lan}<br>
                <a href="{href}" target="_blank">Visa på Hundlistan</a><br>
                {f'<a href="{hemsida_url}" target="_blank">Hemsida</a>' if hemsida_url else ''}
                """.strip()
    
                features.append({
                    "type": "Feature",
                    "geometry": {"type": "Point", "coordinates": [lng, lat]},
                    "properties": {
                        "id": data_id,
                        "namn": title,
                        "adress": address,
                        "lan": lan,
                        "url": href,
                        "hemsida": hemsida_url,
                        "popup": popup_html
                    }
                })
    
            except Exception as e:
                print(f"\n⚠️ Fel vid parsing: {e}")
    
        # --- Spara efter varje sida (inkrementellt)
        geojson = {"type": "FeatureCollection", "features": features}
        with open(OUTFILE, "w", encoding="utf-8") as f:
            json.dump(geojson, f, ensure_ascii=False, indent=2)
        print(f"\n💾 Sparade {len(features)} poster efter sida {page}.")

        print(f"\n✅ Klart! Totalt {len(features)} hundparker sparade i {OUTFILE}")


🚫 Offline-läge: inga nya data hämtas.


In [3]:
import pandas as pd
dfHundlistan = pd.json_normalize(features) 

## Extract from OSM

In [4]:
import requests
import json
import os
import time

# 🗺️ Overpass API
overpass_url = "https://overpass-api.de/api/interpreter"
sweden_bbox = "55.0,10.5,69.2,24.2"

# 🔍 Fråga – alltid samma
overpass_query = f"""
[out:json][timeout:60];
nwr["leisure"="dog_park"]({sweden_bbox});
out center;
"""

# 💾 Cacheinställningar
cache_file = "osm_dogparks_cache.json"
cache_ttl = 60 * 60 * 24 * 7  # 7 dagar i sekunder

# 🧠 Funktion med cache
def get_osm_dogparks():
    if os.path.exists(cache_file):
        age = time.time() - os.path.getmtime(cache_file)
        if age < cache_ttl:
            print("📦 Läser hundrastgårdar från cache...")
            with open(cache_file, "r", encoding="utf-8") as f:
                return json.load(f)
        else:
            print("⚠️ Cache äldre än 7 dagar — hämtar ny data...")

    print("🌍 Hämtar hundrastgårdar från OSM...")
    response = requests.get(overpass_url, params={"data": overpass_query})
    response.raise_for_status()
    data = response.json()

    # 💾 Spara till cache
    with open(cache_file, "w", encoding="utf-8") as f:
        json.dump(data, f, ensure_ascii=False, indent=2)

    print(f"✅ Sparade {len(data['elements'])} objekt till cache.")
    return data


# 🚀 Kör
osm_data = get_osm_dogparks()
print(f"🐾 Hittade {len(osm_data['elements'])} hundrastgårdar.")


📦 Läser hundrastgårdar från cache...
🐾 Hittade 912 hundrastgårdar.


In [5]:
# Steg 1: Samlar alla node-ID som används som byggstenar i en way/relation.
# Steg 2: Filtrerar bort dessa “interna” noder men behåller alla andra.
# Steg 3: Gör ett rent DataFrame med id, type, lat, lon och alla taggar.
import pandas as pd

# 1️⃣ Hämta alla node-ID som används i en way eller relation
used_node_ids = set()

for el in osm_data["elements"]:
    if el["type"] in ("way", "relation"):
        for ref in el.get("nodes", []):
            used_node_ids.add(ref)
        for member in el.get("members", []):
            if member.get("type") == "node":
                used_node_ids.add(member["ref"])

# 2️⃣ Behåll allt som inte är en node ELLER noder som inte används
filtered_elements = []
for el in osm_data["elements"]:
    if el["type"] != "node" or el["id"] not in used_node_ids:
        filtered_elements.append(el)

print(f"Före: {len(osm_data['elements'])}, Efter: {len(filtered_elements)}")

# 3️⃣ (valfritt) skapa DataFrame
rows = []
for el in filtered_elements:
    if el["type"] == "node":
        lat = el.get("lat")
        lon = el.get("lon")
    else:
        lat = el.get("center", {}).get("lat")
        lon = el.get("center", {}).get("lon")

    row = {
        "id": el.get("id"),
        "type": el.get("type"),
        "lat": lat,
        "lon": lon
    }
    row.update(el.get("tags", {}))
    rows.append(row)

dfOSM = pd.DataFrame(rows)
print(dfOSM.head())


Före: 912, Efter: 912
          id  type        lat        lon created_by   leisure  \
0  254731144  node  63.849216  23.119295       JOSM  dog_park   
1  852972410  node  57.268053  17.055340        NaN  dog_park   
2  861388751  node  59.457830  15.395399        NaN  dog_park   
3  871868060  node  59.365317  16.426522        NaN  dog_park   
4  874337325  node  60.053820  18.752540        NaN  dog_park   

           description                       name alt_name website  ...  \
0                  NaN                        NaN      NaN     NaN  ...   
1  Bath place for dogs                        NaN      NaN     NaN  ...   
2                  NaN       Frövi brukshundklubb      NaN     NaN  ...   
3                  NaN  Eskilstuna Brukshundklubb      NaN     NaN  ...   
4                  NaN      Haverö Brukshundklubb      NaN     NaN  ...   

  gate:type dog_park:picnic_table kartaview mapillary contact:phone  \
0       NaN                   NaN       NaN       NaN           N

In [6]:
### Stockholms stad

In [7]:
import geopandas as gpd

# Läs in geopackage-filen
gdf = gpd.read_file("Hundrastgard_Yta.gpkg")

# Visa grundläggande information
print(gdf.head())
print(gdf.crs)
print(gdf.columns)


def convert_misread_date(x):
    try:
        if pd.isna(x):
            return None
        # gör till int, ta bara siffrorna
        s = str(int(float(x)))
        # om 8 tecken → YYYYMMDD
        if len(s) == 8:
            return pd.to_datetime(s, format="%Y%m%d", errors="coerce")
        return None
    except Exception:
        return None

for col in [c for c in gdf.columns if "DATE" in c.upper()]:
    gdf[col + "_fmt"] = gdf[col].apply(convert_misread_date)


   Anläggningsår      Area   CHANGE_DATE           CID   CREATE_DATE  \
0            NaN  4828.314  2.020051e+11  1.738443e+15  2.020051e+11   
1            NaN   982.746  2.020051e+11  1.738448e+15  2.020051e+11   
2            NaN   950.420  2.020051e+11  1.738446e+15  2.020051e+11   
3         2011.0   997.487  2.020051e+11  1.738443e+15  2.020051e+11   
4         2018.0   200.337  2.022032e+11  1.738442e+15  2.020051e+11   

   FEATURE_TYPE_OBJECT_ID  FEATURE_TYPE_VERSION_ID Huvudman  \
0                17314453                        1      SdF   
1                17314453                        1      SdF   
2                17314453                        1      SdF   
3                17314453                        1      SdF   
4                17314453                        1      SdF   

                                       ID MAIN_ATTRIBUTE_DESCRIPTION  \
0                                    None                        SdF   
1                                 Ekhagen   

/Library/Frameworks/Python.framework/Versions/3.12/lib/python3.12/site-packages/pyogrio/raw.py:198: RuntimeWarning: GPKG: unrecognized user_version=0x00000000 (0) on 'Hundrastgard_Yta.gpkg'
  return ogr_read(


In [8]:
import geopandas as gpd
import pandas as pd

# Läs in
gdf = gpd.read_file("Hundrastgard_Yta.gpkg")

# Beräkna centroid i meter-CRS (SWEREF99 TM) och konvertera till WGS84
gdf_proj = gdf.to_crs(epsg=3006)
gdf["geometry_centroid"] = gdf_proj.geometry.centroid.to_crs(epsg=4326)

# Lägg till lat/lon
gdf["lon"] = gdf["geometry_centroid"].x
gdf["lat"] = gdf["geometry_centroid"].y

# Lista möjliga datumkolumner
date_cols = [c for c in gdf.columns if "DATE" in c.upper() or "DATUM" in c.upper()]
print("🕒 Datumkolumner:", date_cols)

# Funktion för att försöka tolka stora siffror som tidsstämplar
def convert_date(x):
    try:
        # Om NaN
        if pd.isna(x):
            return None
        # Om redan datetime
        if isinstance(x, pd.Timestamp):
            return x
        # Om det ser ut som 1.738443e+15 (millisekunder)
        x = float(x)
        if x > 1e12:  # troligen millisekunder
            return pd.to_datetime(x, unit="ms")
        elif x > 1e9:  # sekunder
            return pd.to_datetime(x, unit="s")
        else:
            return None
    except Exception:
        return None

# Konvertera alla identifierade datumfält
for col in date_cols:
    gdf[col + "_fmt"] = gdf[col].apply(convert_date)

# Visa exempel på konverterade datum
print(gdf[[c for c in gdf.columns if "DATE" in c or "fmt" in c]].head())

gdf.drop(columns=["geometry", "geometry_centroid"]).to_csv("hundrastgardar_fix.csv", index=False)
print("✅ Sparade 'hundrastgardar_fix.csv' med riktiga datum och koordinater")


🕒 Datumkolumner: ['CHANGE_DATE', 'CREATE_DATE']
    CHANGE_DATE   CREATE_DATE CHANGE_DATE_fmt CREATE_DATE_fmt
0  2.020051e+11  2.020051e+11            None            None
1  2.020051e+11  2.020051e+11            None            None
2  2.020051e+11  2.020051e+11            None            None
3  2.020051e+11  2.020051e+11            None            None
4  2.022032e+11  2.020051e+11            None            None
✅ Sparade 'hundrastgardar_fix.csv' med riktiga datum och koordinater


/Library/Frameworks/Python.framework/Versions/3.12/lib/python3.12/site-packages/pyogrio/raw.py:198: RuntimeWarning: GPKG: unrecognized user_version=0x00000000 (0) on 'Hundrastgard_Yta.gpkg'
  return ogr_read(


## Skapa karta 

In [9]:
import folium
import json
import pandas as pd
from datetime import datetime
gdf = gdf.to_crs(epsg=4326)
# --------------------------------------------------
# 🗺️ 1. Grundkarta (centrerad över Sverige)
# --------------------------------------------------
m = folium.Map(location=[62.0, 16.0], zoom_start=5, tiles="OpenStreetMap")

# --------------------------------------------------
# 🐾 2. Hundlistan (dfHundlistan)
# --------------------------------------------------
hund_layer = folium.FeatureGroup(name="🐾 Hundparker (Hundlistan)")

for _, row in dfHundlistan.iterrows():
    coords = row["geometry.coordinates"]
    if not isinstance(coords, (list, tuple)) or len(coords) != 2:
        continue
    lon, lat = coords
    namn = row["properties.namn"]
    adress = row.get("properties.adress", "Okänd adress")
    lan = row.get("properties.lan", "Okänt län")
    url = row.get("properties.url", "")

    popup_html = f"""
    <div style="font-family: Arial; font-size: 13px;">
      <b style="font-size:14px; color:#2b7a78;">🐾 {namn}</b><br>
      <span style="color:#555;">📍 {adress}</span><br>
      <span style="color:#555;">🏙️ {lan}</span><br>
      <span style="color:#777;">🧭 {lat:.5f}, {lon:.5f}</span><br><br>
      <a href="{url}" target="_blank" style="color:#0077cc;">🔗 Visa på Hundlistan</a><br>
      <a href="https://www.openstreetmap.org/#map=17/{lat:.5f}/{lon:.5f}&layers=N"
         target="_blank" style="color:#d97706;">🗺️ Skapa OSM Note här</a>
    </div>
    """

    folium.Marker(
        [lat, lon],
        popup=folium.Popup(popup_html, max_width=280),
        tooltip=namn,
        icon=folium.Icon(color="green", icon="paw", prefix="fa")
    ).add_to(hund_layer)

hund_layer.add_to(m)

# --------------------------------------------------
# 🐕 3. OSM-hundrastgårdar (dfOSM)
# --------------------------------------------------
osm_layer = folium.FeatureGroup(name="🐶 Hundrastgårdar (OSM)")

for _, row in dfOSM.iterrows():
    lat, lon = row["lat"], row["lon"]
    if pd.isna(lat) or pd.isna(lon):
        continue

    name = row.get("name", "Okänd rastgård")
    osm_id = row["id"]
    osm_type = row["type"]

    popup_html = f"""
    <div style="font-family: Arial; font-size: 13px;">
      <b style="font-size:14px; color:purple;">🐕 {name}</b><br>
      <span style="color:#777;">🧭 {lat:.5f}, {lon:.5f}</span><br>
      <details>
        <summary style="color:#0077cc; cursor:pointer;">📋 Visa mer info</summary>
        <p>
          <b>OSM-ID:</b> {osm_id}<br>
          <a href="https://www.openstreetmap.org/{osm_type}/{osm_id}" 
             target="_blank" style="color:#0077cc;">🔗 Öppna i OSM</a>
        </p>
      </details>
    </div>
    """

    folium.Marker(
        [lat, lon],
        popup=folium.Popup(popup_html, max_width=280),
        tooltip=name,
        icon=folium.Icon(color="purple", icon="paw", prefix="fa")
    ).add_to(osm_layer)

osm_layer.add_to(m)


# --------------------------------------------------
# 📦 5. Info-box (collapsible)
# --------------------------------------------------
# --------------------------------------------------
# 🐾 2. Infobox (öppen från start, collapsible)
# --------------------------------------------------
from datetime import datetime
created = datetime.now().strftime("%Y-%m-%d kl. %H:%M")

info_html = f"""
<style>
#infoBox {{
  position: fixed;
  top: 10px;
  left: 10px;
  z-index: 9999;
  background-color: rgba(255,255,255,0.97);
  padding: 10px 12px;
  border-radius: 12px;
  box-shadow: 0 0 10px rgba(0,0,0,0.3);
  font-family: Arial, sans-serif;
  font-size: 13px;
  max-width: 260px;
  transition: all 0.3s ease-in-out;
}}
#toggleBtn {{
  background-color: #0077cc;
  color: white;
  border: none;
  border-radius: 8px;
  padding: 6px 10px;
  cursor: pointer;
  font-size: 13px;
  width: 100%;
  text-align: center;
}}
#toggleBtn:hover {{ background-color: #005fa3; }}
#infoContent {{ display: block; margin-top: 8px; }}
.version-list {{
  text-align: left;
  margin-top: 10px;
  padding-left: 12px;
}}
.version-list a {{
  color: #0077cc;
  text-decoration: none;
}}
.version-list a:hover {{
  text-decoration: underline;
}}
.version-list li {{
  margin-bottom: 4px;
}}
@media (max-width: 600px) {{
  #infoBox {{ max-width: 190px; font-size: 12px; }}
}}
</style>

<div id="infoBox">
  <button id="toggleBtn">❌ Dölj info</button>
  <div id="infoContent">
    <div style="text-align:center;">
      <img src="https://raw.githack.com/salgo60/Dogpark_Sweden/main/DogparkSweden_2.jpg"
           alt="Dogpark Sweden" width="180" style="border-radius:8px; margin-bottom:5px;"><br>
      <a href="https://github.com/salgo60/Dogpark_Sweden"
         target="_blank"
         style="color:#0077cc; font-weight:bold; text-decoration:none;">
         🐾 GITHUB where the magic happens
      </a>
    </div>

    <hr style="margin:10px 0; border:none; border-top:1px solid #ccc;">
    <b style="display:block; text-align:center;">📌 Versioner</b>
    <ol class="version-list">
      <li><a href="https://raw.githack.com/salgo60/Dogpark_Sweden/main/notebook/hundparker_folium_snygg_1.html" target="_blank">Hundlistan</a></li>
      <li><a href="https://raw.githack.com/salgo60/Dogpark_Sweden/main/notebook/hundparker_folium_snygg_2.html" target="_blank">Hundlista med info box</a></li>
      <li><a href="https://raw.githack.com/salgo60/Dogpark_Sweden/main/notebook/hundparker_folium_snygg_3.html" target="_blank">Hundlistan + OpenStreetMap-lager</a></li>
      <li><a href="https://raw.githack.com/salgo60/Dogpark_Sweden/main/notebook/hundparker_folium_snygg_3_2.html" target="_blank">🌍 Hundlistan + OSM-version</a></li>
      <li><a href="https://raw.githack.com/salgo60/Dogpark_Sweden/main/notebook/hundparker_folium_snygg_3_4.html" target="_blank">📍 Min plats bottomright</a></li>
      <li><a href="https://raw.githack.com/salgo60/Dogpark_Sweden/main/notebook/hundparker_folium_snygg_3_6.html" target="_blank">📍 Stockholms stads Öppna data</a></li>
    </ol>

    <div style="text-align:center; margin-top:8px;">
      <a href="https://youtu.be/3gnYR1_PKNI" target="_blank"
         style="color:#cc0000; text-decoration:none; font-weight:bold;">
         🎥 Video: Hur du skapar en OSM Note
      </a><br>
      <span style="color:#555; font-size:11px;">🕒 Skapad {created}</span>
    </div>
  </div>
</div>

<script>
  const btn = document.getElementById('toggleBtn');
  const content = document.getElementById('infoContent');
  let open = true;
  btn.onclick = () => {{
    open = !open;
    content.style.display = open ? 'block' : 'none';
    btn.innerText = open ? '❌ Dölj info' : '📖 Visa info';
  }};
</script>
"""


m.get_root().html.add_child(folium.Element(info_html))

# --------------------------------------------------
# 📍 6. “Min plats”-knapp (geolocation)
# --------------------------------------------------
geolocate_js = """
<script>
function addLocateButton(map){
  const btn = L.control({position: 'bottomright'});
  btn.onAdd = function(){
    const div = L.DomUtil.create('div', 'leaflet-bar leaflet-control leaflet-control-custom');
    div.innerHTML = '📍<br><small style="font-size:10px;">Min plats</small>';
    div.style.backgroundColor = 'white';
    div.style.cursor = 'pointer';
    div.style.textAlign = 'center';
    div.style.padding = '4px';
    div.title = 'Visa min plats';
    div.onclick = function(){
      if (navigator.geolocation){
        navigator.geolocation.getCurrentPosition(
          function(pos){
            const lat = pos.coords.latitude;
            const lon = pos.coords.longitude;
            const userMarker = L.marker([lat, lon], {
              icon: L.icon({
                iconUrl: 'https://cdn-icons-png.flaticon.com/512/64/64113.png',
                iconSize: [24, 24]
              })
            }).addTo(map);
            userMarker.bindPopup('📍 Du är här!<br><b>Lat:</b> '+lat.toFixed(5)+'<br><b>Lon:</b> '+lon.toFixed(5)).openPopup();
            map.setView([lat, lon], 14);
          },
          function(err){ alert('Kunde inte hämta position: ' + err.message); }
        );
      } else {
        alert('Geolocation stöds inte av din webbläsare.');
      }
    };
    return div;
  };
  btn.addTo(map);
}
setTimeout(function() {
  for (const key in window) {
    if (key.startsWith("map_")) {
      addLocateButton(window[key]);
      break;
    }
  }
}, 500);
</script>
"""
m.get_root().html.add_child(folium.Element(geolocate_js))

# --------------------------------------------------
# 🧭 7. Legend (färger och symboler)
# --------------------------------------------------
legend_html = """
<div style="
  position: fixed; 
  bottom: 30px; left: 10px; 
  z-index: 9999; 
  background: white; 
  border-radius: 10px; 
  padding: 8px 10px;
  font-family: Arial; 
  font-size: 13px;
  box-shadow: 0 0 6px rgba(0,0,0,0.3);
">
<b>🗺️ Lager</b><br>
<span style='color:green;'>🟢</span> Hundlistan<br>
<span style='color:purple;'>🟣</span> OSM-hundrastgårdar<br>
<span style='color:#ff6600;'>🟠</span> Stockholms stads öppna data
</div>
"""
m.get_root().html.add_child(folium.Element(legend_html))

# --------------------------------------------------
# 🎛️ 8. Layer Control + Spara
# --------------------------------------------------
#folium.LayerControl(collapsed=False).add_to(m)

outfile = "output/SAT225_hundparker.html"

#m.save(outfile)
print(f"✅ Klar: {outfile}")


✅ Klar: output/SAT225_hundparker.html


In [10]:
m

In [11]:
print(gdf.geom_type.value_counts())

Polygon    88
Name: count, dtype: int64


In [12]:
gdf.geometry.type.value_counts()

Polygon    88
Name: count, dtype: int64

In [13]:
import folium
import geopandas as gpd
from shapely.geometry import Point, LineString, Polygon, MultiPolygon

# 🧹 Remove extra geometry columns (only keep one active geometry)
geom_cols = [
    c for c in gdf.columns
    if gdf[c].apply(lambda x: isinstance(x, (Point, LineString, Polygon, MultiPolygon))).any()
]
print("🧹 Removing geometry-type columns:", geom_cols)
gdf_clean = gdf.drop(columns=geom_cols, errors="ignore")

# 🟠 Create feature group
stad_layer = folium.FeatureGroup(name="🟠 Stockholms stad (öppna data)")

# ---------------------------------------------------------
# 🧭 1. Draw all polygons (and multipolygons) together
# ---------------------------------------------------------
poly_gdf = gdf[gdf.geometry.geom_type.isin(["Polygon", "MultiPolygon"])]

if not poly_gdf.empty:
    folium.GeoJson(
        data=poly_gdf.__geo_interface__,
        style_function=lambda x: {
            "fillColor": "#ff6600",
            "color": "#cc5500",
            "weight": 2,
            "fillOpacity": 0.3,
        },
        tooltip=folium.GeoJsonTooltip(
            fields=[c for c in gdf_clean.columns if c != "geometry"],
            aliases=[f"{c}:" for c in gdf_clean.columns if c != "geometry"],
            sticky=False,
            localize=True,
        ),
        name="🟠 Stockholms stad (öppna data)"
    ).add_to(stad_layer)

# ---------------------------------------------------------
# 🐾 2. Add paw markers for polygons' centroids
# ---------------------------------------------------------
for _, row in poly_gdf.iterrows():
    geom = row.geometry
    if geom.is_empty:
        continue
    if geom.geom_type == "MultiPolygon":
        geom = max(geom.geoms, key=lambda g: g.area)
    centroid = geom.centroid
    lat, lon = centroid.y, centroid.x
    name = row.get("FEATURE_TYPE_NAME", "Okänd plats")

    popup_html = f"""
    <div style='font-family:Arial; font-size:13px;'>
      <b style='color:#cc5500;'>🟠 {name}</b><br>
      <span style='color:#777;'>🧭 {lat:.5f}, {lon:.5f}</span><br>
      <a href='https://www.openstreetmap.org/#map=18/{lat:.5f}/{lon:.5f}' 
         target='_blank' style='color:#0077cc;'>📍 Öppna i OSM</a>
    </div>
    """

    folium.Marker(
        [lat, lon],
        popup=folium.Popup(popup_html, max_width=250),
        tooltip=name,
        icon=folium.Icon(color="orange", icon="paw", prefix="fa")
    ).add_to(stad_layer)

# ---------------------------------------------------------
# 📍 3. Add any Point geometries (e.g. small facilities)
# ---------------------------------------------------------
point_gdf = gdf[gdf.geometry.geom_type == "Point"]

for _, row in point_gdf.iterrows():
    geom = row.geometry
    lat, lon = geom.y, geom.x
    name = row.get("FEATURE_TYPE_NAME", "Okänd plats")

    folium.CircleMarker(
        location=[lat, lon],
        radius=6,
        color="#cc5500",
        fill=True,
        fill_color="#ff6600",
        fill_opacity=0.8,
        tooltip=name,
    ).add_to(stad_layer)

# ---------------------------------------------------------
# 🎛️ 4. Add to map
# ---------------------------------------------------------
stad_layer.add_to(m)
folium.LayerControl(collapsed=False).add_to(m)


🧹 Removing geometry-type columns: ['geometry', 'geometry_centroid']


In [14]:
print(gdf.crs)

EPSG:4326


In [15]:
m

TypeError: Object of type Point is not JSON serializable

In [16]:
#m.save("hundparker_folium_snygg.html") 
m.save("hundparker_folium_snygg_3_7.html")

In [17]:
import geopandas as gpd
import pandas as pd
import folium

# --------------------------------------------------
# 1️⃣ Läs in och fixa koordinater
# --------------------------------------------------
gdf = gpd.read_file("Hundrastgard_Yta.gpkg")

# Beräkna centroid i SWEREF99 TM (EPSG:3006) → tillbaka till WGS84 (EPSG:4326)
gdf_proj = gdf.to_crs(epsg=3006)
centroids = gdf_proj.geometry.centroid.to_crs(epsg=4326)

gdf["lon"] = centroids.x
gdf["lat"] = centroids.y

# --------------------------------------------------
# 2️⃣ Fixa datumen (YYYYMMDD → datetime)
# --------------------------------------------------
def convert_misread_date(x):
    try:
        if pd.isna(x):
            return None
        s = str(int(float(x)))
        if len(s) == 8:
            return pd.to_datetime(s, format="%Y%m%d", errors="coerce")
        return None
    except Exception:
        return None

for col in [c for c in gdf.columns if "DATE" in c.upper()]:
    gdf[col + "_fmt"] = gdf[col].apply(convert_misread_date)

# --------------------------------------------------
# 3️⃣ Skapa enkel Folium-karta
# --------------------------------------------------
# Centrera över Sverige
m_s = folium.Map(location=[62.0, 16.0], zoom_start=5, tiles="CartoDB positron")

# Lägg till punkter
for _, row in gdf.iterrows():
    lat, lon = row["lat"], row["lon"]
    if pd.isna(lat) or pd.isna(lon):
        continue

    namn = row.get("ID") or row.get("NAMN") or row.get("MAIN_ATTRIBUTE_DESCRIPTION", "Okänd")
    create_date = row.get("CREATE_DATE_fmt")
    change_date = row.get("CHANGE_DATE_fmt")

    popup_html = f"""
    <div style="font-family:Arial; font-size:13px;">
      <b style="font-size:14px;">🐾 {namn}</b><br>
      🧭 {lat:.5f}, {lon:.5f}<br>
      📅 Skapad: {create_date if pd.notna(create_date) else '-'}<br>
      🔁 Ändrad: {change_date if pd.notna(change_date) else '-'}
    </div>
    """

    folium.CircleMarker(
        location=[lat, lon],
        radius=5,
        color="#2b7a78",
        fill=True,
        fill_opacity=0.8,
        popup=folium.Popup(popup_html, max_width=250),
        tooltip=namn
    ).add_to(m)

# --------------------------------------------------
# 4️⃣ Visa + spara
# --------------------------------------------------
#m_s.save("Sthlm_open_data_hundrastgardar.html")
print("✅ Klar! Sparad som Sthlm_open_data_hundrastgardar")
m_s



✅ Klar! Sparad som Sthlm_open_data_hundrastgardar


/Library/Frameworks/Python.framework/Versions/3.12/lib/python3.12/site-packages/pyogrio/raw.py:198: RuntimeWarning: GPKG: unrecognized user_version=0x00000000 (0) on 'Hundrastgard_Yta.gpkg'
  return ogr_read(


In [18]:
print(gdf.geom_type.value_counts())

Polygon    88
Name: count, dtype: int64


In [19]:
# --------------------------------------------------
# 🟠 Stockholms stad – Hundrastgårdar (öppna data)
# --------------------------------------------------

stad_layer = folium.FeatureGroup(name="🟠 Hundrastgårdar (Stockholms stad)")

for _, row in gdf.iterrows():
    lat, lon = row["lat"], row["lon"]
    if pd.isna(lat) or pd.isna(lon):
        continue

    namn = row.get("ID") or row.get("MAIN_ATTRIBUTE_DESCRIPTION", "Okänd rastgård")
    create_date = row.get("CREATE_DATE_fmt")
    change_date = row.get("CHANGE_DATE_fmt")

    popup_html = f"""
    <div style="font-family:Arial; font-size:13px;">
      <b style="font-size:14px; color:#ff6600;">🟠 {namn}</b><br>
      🧭 {lat:.5f}, {lon:.5f}<br>
      📅 Skapad: {create_date if pd.notna(create_date) else '-'}<br>
      🔁 Ändrad: {change_date if pd.notna(change_date) else '-'}
    </div>
    """

    folium.CircleMarker(
        location=[lat, lon],
        radius=6,
        color="#ff6600",
        fill=True,
        fill_opacity=0.7,
        popup=folium.Popup(popup_html, max_width=250),
        tooltip=namn
    ).add_to(stad_layer)

stad_layer.add_to(m)


In [20]:
m_s


In [21]:
 # End timer and calculate duration
end_time = time.time()
elapsed_time = end_time - start_time# Bygg audit-lager för den här etappen

# Print current date and total time
print("Date:", datetime.now().strftime("%Y-%m-%d %H:%M:%S"))
minutes, seconds = divmod(elapsed_time, 60)
print("Total time elapsed: {:02.0f} minutes {:05.2f} seconds".format(minutes, seconds))


Date: 2025-10-07 17:34:30
Total time elapsed: 00 minutes 04.07 seconds
